In [162]:
import numpy as np
import os
import librosa
import IPython.display as ipd 

In [93]:
# BASE_DIR = "/Users/gina0/Desktop/fourier_analysis/capstone/sound_folder"
# piano_c5_file = "piano_c5.wav"
# ipd.Audio(os.path.join(BASE_DIR, piano_c5_file))

In [94]:
BASE_DIR_MAC = "/Users/jinahyoo/Desktop/fourier_analysis/capstone/sound_folder"
piano_c5_file = "piano_c5.wav"
ipd.Audio(os.path.join(BASE_DIR_MAC, piano_c5_file))

In [95]:
# Clip the audio to 1 sec
piano_c5_data, sr = librosa.load(os.path.join(BASE_DIR_MAC, piano_c5_file)) #len(piano_c5_data) = 44604; sr = 22050 
piano_c5_clip_1s = piano_c5_data[:22050]
ipd.Audio(piano_c5_clip_1s, rate = sr)

In [97]:
# Plot time domain graph
time = np.arange(0, len(piano_c5_clip_1s)) / sr

In [124]:
# PLoting Absolute One Sided
import plotly.graph_objects as go
def interactivePlotAbsolute(x,y,xlabel,ylabel,title,mode):
    N = len(x)
    graph = go.Figure(
        data = go.Scatter(
            x=x, 
            y=y, 
            mode=mode,
            marker=dict(
                color='MediumPurple',
                size=7,
            ),
            line=dict(
                color='black'
            ))
        )
    graph.update_layout(
        title={
            'text': title,
            'x': 0.5,
            'xanchor': 'center',
            'yanchor': 'top',
            'font':{
                'family': 'Raleway',
                'size': 24,
                'color': 'black'
            }
        },
        xaxis=dict(
            title=xlabel,
        ),
        yaxis=dict(
            title=ylabel
        )
    )
    return graph

In [125]:
# Plot original c5 audio
graph = interactivePlotAbsolute(
    x = time, 
    y = piano_c5_clip_1s, 
    xlabel='Time',
    ylabel='Amplitude',
    mode='lines',
    title='Audio Waveform (Piano C5)')
graph.update_traces(line=dict(color='LightSkyBlue'))
graph.show()

In [306]:
# Add random noise and plot
noise_level = 0.4
noisy_clip = piano_c5_clip_1s + noise_level * np.random.randn(len(piano_c5_clip_1s))
graph = interactivePlotAbsolute(
    x = time, 
    y = noisy_clip, 
    xlabel='Time',
    ylabel='Amplitude',
    mode='lines',
    title='Audio Waveform (Piano C5)')
graph.update_traces(line=dict(color='LightSkyBlue'))
graph.show()

In [307]:
# Play noisy sound
ipd.Audio(noisy_clip, rate = sr)

## DFT
$$\begin{align}
\Upsilon_p &=  \sum_{n=0}^{N-1} y_n e^{-2\pi ipn/N}\\
y_n &= \frac{1}{2N} \sum_{p=0}^{N-1}\Upsilon_pe^{2\pi ipn/N}
\end{align}$$

Here, $\Upsilon_p$ denotes the DFT (Discrete Fourier Transform), and $y_n$ is the IDFT (Inverse Discrete Fourier Transform), representing the discrete signal at index $n$ in the time domain. The DFT essentially computes how much of each sine and cosine wave (of varying frequencies indexed by $p$) is present in the input signal $y_n$.

The DFT involves multiplying each time-domain signal value $y_n$ with sine and cosine basis functions of different frequencies (represented by $p$) and summing the result. Due to the nested summation over $N$ time samples and $N$ frequency bins, the time complexity of a naive DFT implementation is $\mathcal{O}(N^2)$, where $N$ is the number of discrete points.

Given that $N = 22050$ for our piano C5 sound clip example, a full DFT computation would require $N^2 = 486,202,500$ operations, which would be computationally expensive.

In the following code, I reduce the outer loop of the DFT to $N/2$ to decrease execution time. Since the DFT output is symmetric, (it reflects across the midpoint for real-valued time-domain signals), it is reasonable to compute only the first half of the frequency spectrum to save computation time.

In [82]:
# apply DFT with numpy
import time
N = len(piano_c5_clip_1s)
T = N / sr #record length(audio time)
freq = np.linspace(0, sr, N)
dft = np.zeros(N, dtype=complex)

start_time = time.time()
for p in range(0, N//2): #reduced the outer loop to N/2
    for n in range(0, N):
        y_j = piano_c5_data[n]
        w_j = np.exp(-1j*2*np.pi*p*n/N)
        dft[p] += (y_j*w_j)
end_time = time.time()
print(f"Execution time: {end_time - start_time:.4f} seconds")

Execution time: 132.3950 seconds


## Analyzing the resut of FFT
### Amplitude Spectrum
Assume that the signal is given by $y_n = Asin(x)$ where $A$ denote the amplitude.

Then, the DFT is:

$$\begin{align}
\Upsilon_p &= \sum_{n=0}^{N-1} A\sin(\frac{2\pi pn}{N}) \cdot \left[\cos(\frac{2\pi pn}{N}) - i\sin(\frac{2\pi pn}{N})\right]\\
&= A \sum_{n=0}^{N-1} \left[(\sin(\frac{2\pi pn}{N}) \cdot \cos(\frac{2\pi pn}{N})) - i\sin^2(\frac{2\pi pn}{N}) \right]\\
\dfrac{\Upsilon_p}{N} &= A \sum_{n=0}^{N-1} \left[\frac{-i\sin^2(\frac{2\pi pn}{N})}{N}\right] = -Ai \sum_{n=0}^{N-1} \left[\frac{\sin^2(\frac{2\pi pn}{N})}{N}\right]\\
&= -\frac{A}{2}i
\end{align}$$

Notice that the first term $(\sum \sin(\frac{2\pi pn}{N}) \cdot \cos(\frac{2\pi pn}{N}))$ vanishes due to the orthogonality of sine and cosine over a complete period $N$.Then we multiply $\frac{1}{N}$ to both sides of the equation. This makes the second summation term $\frac{\sin^2(\frac{2\pi pn}{N})}{N}$ to be the average of $\sin^2(\frac{2\pi pn}{N})$ over the complete period, which is $\dfrac{1}{2}$.

Now we take the absolute value of $\Upsilon_p$ to get the half of the amplitude:
$$ |\frac{\Upsilon_p}{N}| = |-\frac{A}{2}i| =\frac{A}{2}.$$

Thus $A = \dfrac{2 |\Upsilon_p|}{N}$ if we only consider one-sided spectrum with the assumtion that the signal is real and symmetric in frequency domain.


### Power Spectrum 
The power spectrum represents the signal power at eacj frequency, and computed as folows:

$$ |\frac{Y_p}{N}|^2 = (\frac{A}{2})^2 = \frac{A^2}{4}$$

In [205]:
piano_c5_dft_as = (np.abs(dft))/ N #One-sided amplitude spectrum
piano_c5_dft_as_one_sided = 2 * piano_c5_dft_as
graph = interactivePlotAbsolute(
    x = freq[:N//2], 
    y = piano_c5_dft_as_one_sided[:N//2], 
    xlabel='Frequency',
    ylabel='Amplitude',
    mode='markers+lines',
    title='Piano C5 DFT - One Sided: abs(DFT(yn))')
graph.show()

In [303]:
from plotly.subplots import make_subplots
# apply FFT to original piano clip
piano_c5_fft = np.fft.fft(piano_c5_clip_1s)

# apply FFT to noisy clip
piano_c5_noisy_fft = np.fft.fft(noisy_clip)
graph_noise_fft = interactivePlotAbsolute(
    x = freq[:N//2], 
    y = abs(piano_c5_noisy_fft[:N//2]), 
    mode ='markers+lines',
    xlabel='Frequency',
    ylabel='Amplitude',
    title = 'Noisy Piano C5 FFT - One Sided: abs(FFT(yn))')
graph_noise_fft.update_traces(marker=dict(color='LightSkyBlue'))
graph_noise_fft.show()
# absolute spectrum 
piano_c5_fft_as = abs(piano_c5_fft)/N #Two-sided amplitude
piano_c5_fft_as_one_side = 2 * piano_c5_fft_as # Double values except for DC and Nyquist
graph_original = interactivePlotAbsolute(
    x = freq[:N//2], 
    y = piano_c5_fft_as_one_side[:N//2], 
    mode ='markers+lines',
    xlabel='Frequency',
    ylabel='Amplitude',
    title = 'Piano C5 FFT - One Sided: abs(FFT(yn))')

piano_c5_noisy_fft_as = abs(piano_c5_noisy_fft)/N #Two-sided amplitude
piano_c5_noisy_fft_as_one_side = 2 * piano_c5_noisy_fft_as # Double values except for DC and Nyquist
graph_noise = interactivePlotAbsolute(
    x = freq[:N//2], 
    y = piano_c5_noisy_fft_as_one_side[:N//2], 
    mode ='markers+lines',
    xlabel='Frequency',
    ylabel='Amplitude',
    title = 'Noisy Piano C5 FFT - One Sided: abs(FFT(yn))')
graph_noise.update_traces(marker=dict(color='LightSkyBlue'))


# power spectrum
piano_c5_fft_ps= (np.abs(piano_c5_fft)**2) * (1/N**2) #Two sided power
piano_c5_fft_ps_one_sided = piano_c5_fft_ps[:N//2].copy()
graph_original_ps = interactivePlotAbsolute(
    x = freq[:N//2], 
    y = piano_c5_fft_ps_one_sided[:N//2], 
    mode ='markers+lines',
    xlabel='Frequency',
    ylabel='Amplitude',
    title = 'Piano C5 FFT - One Sided Power Spectrum')
graph_original_ps.update_traces(marker=dict(color='#54AB4B'))

piano_c5_noise_ps_fft_ps = (np.abs(piano_c5_noisy_fft) ** 2) / N**2 #Two sided power
piano_c5_noise_fft_ps_one_sided = piano_c5_noise_ps_fft_ps[:N//2].copy()
graph_noise_ps = interactivePlotAbsolute(
    x = freq[:N//2], 
    y = piano_c5_noise_fft_ps_one_sided, 
    mode ='markers+lines',
    xlabel='Frequency',
    ylabel='Amplitude',
    title = 'Piano C5 FFT - One Sided Power Spectrum')
graph_noise_ps.update_traces(marker=dict(color='#ff7f0e'))

#Subplots
combined_graphs = make_subplots(rows=2, cols=2, subplot_titles=('Piano C5 FFT', 'Noisy Piano C5 FFT', 'Piano C5 FFT PS', 'Noisy Piano C5 FFT PS'))
combined_graphs.add_traces(graph_original.data, rows=1, cols=1)
combined_graphs.add_traces(graph_noise.data, rows=1, cols=2)
combined_graphs.add_traces(graph_original_ps.data, rows=2, cols=1)
combined_graphs.add_traces(graph_noise_ps.data, rows=2, cols=2)

combined_graphs.data[0].name = "Original Absolute Spectrum"
combined_graphs.data[1].name = "Noise Absolute Spectrum"
combined_graphs.data[2].name = "Original Power Spectrum"
combined_graphs.data[3].name = "Noise Power Spectrum"
combined_graphs.show()

In [312]:
half_mask = piano_c5_noise_fft_ps_one_sided > 0.000048
full_mask = np.zeros(len(piano_c5_noisy_fft), dtype=bool)
full_mask[:len(half_mask)] = half_mask
full_mask[-len(half_mask)+1:] = half_mask[1:][::-1] 
fhat = full_mask * piano_c5_noisy_fft
psd_ifft = np.fft.ifft(fhat)


graph_original = interactivePlotAbsolute(
    x = freq[:N//2], 
    y = np.abs(fhat[:N//2]), 
    mode ='markers+lines',
    xlabel='Frequency',
    ylabel='Amplitude',
    title = 'Piano C5 FFT - One Sided: abs(FFT(yn))')
graph_original.show()

time = np.arange(0, len(piano_c5_clip_1s)) / sr


fig = go.Figure()

fig.add_trace(go.Scatter(
    x=time,
    y=np.real(psd_ifft),
    mode='lines',
    name='Filtered (IFFT)',
    line=dict(color='rgba(144, 238, 144, 0.9)'), 
))

fig.add_trace(go.Scatter(
    x=time,
    y=piano_c5_clip_1s,
    mode='lines',
    name='Original Clean',
    line=dict(color='rgba(83, 137, 245, 0.4)'),  
))

fig.add_trace(go.Scatter(
    x=time,
    y=noisy_clip,
    mode='lines',
    name='Noisy Input',
    line=dict(color='rgba(217, 0, 58, 0.2)'), 
))

fig.update_layout(
    title={
        'text':'Original, Noisy, and Filtered Signal',
        'x': 0.5},
    xaxis_title='Time (s)',
    yaxis_title='Amplitude',
    font=dict(family="Arial", size=14)
)

fig.show()

In [308]:
ipd.Audio(np.real(psd_ifft), rate=sr)